## Scrape and clean a dataframe of statistics for past and upcoming UFC fights.

**Website Schema**
- /statistics/events/completed?page=X - pages of past UFC events. The first record of the first page is the next upcoming UFC event.

- /event-details/ - the home page links to each past event.

- /fight-details/ - the event details page links to each fight. Per event, there are several fights and one title fight.

In [1]:
import pandas as pd
import numpy as np

from bs4 import BeautifulSoup
# import requests

from urllib.request import urlopen
from urllib.error import HTTPError
from urllib.error import URLError
import re

In [2]:

def get_bs(url):
    """Get the BeautifulSoup html object of a url"""
    try:
        html = urlopen(url)
        bs = BeautifulSoup(html.read(), 'html.parser')
    except HTTPError as e:
        print(e)
        
    return bs


def find_all_urls(bs, regex_condition = '.+/fight-details/.+'):
    """Return a set of unique urls in a BeautifulSoup html object with a regex search condition"""
    urls = set()
    
    find_all_results = bs.find_all('a', href = re.compile(regex_condition))

    if len(find_all_results) != 0:
        for u in find_all_results:
            if 'href' in u.attrs:
                url = u.attrs['href']
                urls.add(url)
    else:
        return []
            
    return urls

# for url in range(len(url_list)):


In [3]:
# bs = get_bs('http://ufcstats.com/event-details/319c15b8aac5bfde')
# get_match_date = bs.find_all('li', {'class': 'b-list__box-list-item'})[0]
# match_date_list =get_match_date.text.split()[1:]

In [4]:

def get_match_details(match_url):
    """Parse /fight-details/ pages as BeautifulSoup objects"""

    # Set up empty lists that will contain all of the features of each player within /fight-details/.
    p1 = []
    p2 = []

    # Web request
    try:
        html = urlopen(match_url)
        bs = BeautifulSoup(html.read(), 'html.parser')
    except HTTPError as e:
        print(e)
        
    # Figher names    
    player_names_and_outcomes = bs.find_all('div', {'class': {'b-fight-details__person'}})
    p1_name = player_names_and_outcomes[0].find('a', {'class': 'b-link b-fight-details__person-link'}).text
    p2_name = player_names_and_outcomes[1].find('a', {'class': 'b-link b-fight-details__person-link'}).text

    p1.append(p1_name)
    p2.append(p2_name)

    # Weight class
    weight_class = bs.find('i', {'class': 'b-fight-details__fight-title'}).text.strip()[:-5]

    p1.append(weight_class)
    p2.append(weight_class)

    if player_names_and_outcomes[0].find('i', {'class': 'b-fight-details__person-status b-fight-details__person-status_style_green'}):
        p1_win = 1
        p2_win = 0
    else:
        p2_win = 1
        p1_win = 0

    p1.append(p1_win)
    p2.append(p2_win)

    # Get the match length. Matches can be 15 or 25 minutes long, affects the ctrl variable.
    time = bs.find( 'i', 
                    {'class': 'b-fight-details__label'}, 
                    text=re.compile(r'(.+Time format.+)'))\
              .next_sibling.strip()

    # Check if the time format is a 5-round fight (25 minutes). Otherwise, it's 3-round.
    pattern = re.compile("5 Rnd")
    if pattern.search(time):
        duration = 25
    else:
        duration = 15

    p1.append(duration)
    p2.append(duration)

    # Collect all relevant stats from /fight-details/.

    tables = bs.find_all('tbody', {'class': 'b-fight-details__table-body'})

    # The first table is the TOTALs table, tbody with class: b-fight-details__table-body
    # Within the table the stats are selected via p with class: b-fight-details__table-text
    # The first two stats are the names which can be skipped.

    if len(tables) > 0:
        totals_table = tables[0].find_all('p', {'class': 'b-fight-details__table-text'})

        for i in range(2, 20): # skip first two records in table which are the players' names

            stat = totals_table[i].text.strip()

            # The stats are in order of player 1, player 2, player 1, player 2. player 1 only has even values.
            if i % 2 != 1:
                if stat[-1] == '%': # if stat is percent as string
                    stat = int(stat[:-1])/100 # convert to numeric
                if stat == '---' or stat == '--':
                    stat = 0
                p1.append(stat)
            else:
                if stat[-1] == '%': # if stat is percent as string
                    stat = int(stat[:-1])/100 # convert to numeric
                if stat == '---' or stat == '--':
                    stat = 0
                p2.append(stat)

        # Significant Strikes Table

        sig_strikes_table = tables[2].find_all('p', {'class': 'b-fight-details__table-text'})

        # Skip first several records which are the players' names and duplicate stats
        for i in range(6, 18):

            stat = sig_strikes_table[i].text.strip()

            if i % 2 != 1:
                p1.append(stat)
            else:
                p2.append(stat)

        # When there is no stat, it shows as '---'. Convert to 0.
        for i in range(len(p1)):
            if p1[i] == '---' or p1[i] == '--':
                p1[i] = 0
            else:
                continue
        for i in range(len(p2)):
            if p2[i] == '---' or p2[i] == '--':
                p2[i] = 0
            else:
                continue

        player_urls = list(find_all_urls(tables[0], regex_condition='.+/fighter-details/.+'))

        p1.append(player_urls[0])
        p2.append(player_urls[1])

        p1_name = p1[0] # player 1 name
        p2_name = p2[0] # player 2 name

        # Create a dictionary of match details

        match_details = {} # Dictionary of match stats

        match_details['player_1_name'] = p1[0].strip()
        match_details['player_2_name'] = p2[0].strip()

        match_details['weight_class'] = p1[1] # weight class of players

        match_details['win'] = int( p1[2] ) # boolean of whether player 1 won

        match_details['duration'] = int( p1[3] ) # duration of match in minutes

        match_details['kd'] = int( p1[4] ) # knock downs
        match_details['o_kd'] = int( p2[4] ) # opponent knock downs

        match_details['ss_hit'] = int( p1[5].split()[0] ) # significant strikes landed
        match_details['ss_att'] = int( p1[5].split()[2] ) # significant strikes attempted
        match_details['o_ss_hit'] = int( p2[5].split()[0] ) # opponent significant strikes landed
        match_details['o_ss_att'] = int( p2[5].split()[2] ) # opponent significant strikes attempted

        match_details['ss_perc']  = float( p1[6] ) # significant strike percentage
        match_details['o_ss_perc'] = float( p2[6] ) # opponent significant strike percentage

        match_details['s_hit'] = int( p1[7].split()[0] ) # strikes landed
        match_details['s_att'] = int( p1[7].split()[2] ) # strikes attempted
        match_details['o_s_att'] = int( p2[7].split()[2] ) # opponent strikes attempted
        match_details['o_s_hit'] = int( p2[7].split()[0] ) # opponent strikes landed

        match_details['td_hit'] = int( p1[8].split()[0] ) # takedowns landed
        match_details['td_att'] = int( p1[8].split()[2] ) # takedowns attempted
        match_details['o_td_hit'] = int( p2[8].split()[0] ) # opponent takedowns landed
        match_details['o_td_att'] = int( p2[8].split()[2] ) # opponent takedowns attempted

        match_details['td_perc']  = float ( p1[9] ) # takedown percentage
        match_details['o_td_perc'] = float( p2[9] ) # opponent takedown percentage

        match_details['sub_att'] = int( p1[10] ) # submission attempts
        match_details['o_sub_att'] = int( p2[10] ) # opponent submission attempts

        match_details['rev'] = int( p1[11] ) # reversals to a takedown
        match_details['o_rev'] = int( p2[11] ) # opponent reversals to a takedown 

        try: # if ctrl is a timestamp, convert to seconds. Otherwise it is 0 and we can ignore the error
            match_details['ctrl'] = int( p1[12].split(':')[0] )  * 60 + int(p1[12].split(':')[1]) # control in seconds
            match_details['o_ctrl'] = int( p2[12].split(':')[0] ) * 60 + int(p2[12].split(':')[1]) # opponent control in seconds
        except:
            match_details['ctrl'] = 0
            match_details['o_ctrl'] = 0

        match_details['ss_head_hit'] = int( p1[13].split()[0] ) # significant strikes to the head landed
        match_details['ss_head_att'] = int( p1[13].split()[2] ) # significant strikes to the head attempted
        match_details['o_ss_head_hit'] = int( p2[13].split()[0] ) # opponent significant strikes to the head landed
        match_details['o_ss_head_att'] = int( p2[13].split()[2] ) # opponent significant strikes to the head attempted

        match_details['ss_body_hit'] = int( p1[14].split()[0] ) # significant strikes to the body landed
        match_details['ss_body_att'] = int( p1[14].split()[2] ) # significant strikes to the body attempted
        match_details['o_ss_body_hit'] = int( p2[14].split()[0] ) # opponent significant strikes to the body landed
        match_details['o_ss_body_att'] = int( p2[14].split()[2] ) # opponent significant strikes to the body attempted

        match_details['ss_leg_hit'] = int( p1[15].split()[0] ) # significant strikes to the leg landed
        match_details['ss_leg_att'] = int( p1[15].split()[2] ) # significant strikes to the leg attempted
        match_details['o_ss_leg_hit'] = int( p2[15].split()[0] ) # opponent significant strikes to the leg landed
        match_details['o_ss_leg_att'] = int( p2[15].split()[2] ) # opponent significant strikes to the leg attempted

        match_details['ss_dist_hit'] = int( p1[16].split()[0] ) # significant strikes at a distance landed
        match_details['ss_dist_att'] = int( p1[16].split()[2] ) # significant strikes at a distance attempted
        match_details['o_ss_dist_hit'] = int( p2[16].split()[0] ) # opponent significant strikes at a distance landed
        match_details['o_ss_dist_att'] = int( p2[16].split()[2] ) # opponent significant strikes at a distance attempted

        match_details['ss_clinch_hit'] = int( p1[17].split()[0] ) # significant strikes in the clinch landed
        match_details['ss_clinch_att'] = int( p1[17].split()[2] ) # significant strikes in the clinch attempted
        match_details['o_ss_clinch_hit'] = int( p2[17].split()[0] ) # opponent significant strikes in the clinch landed
        match_details['o_ss_clinch_att'] = int( p2[17].split()[2] ) # opponent significant strikes in the clinch attempted

        match_details['ss_ground_hit'] = int( p1[18].split()[0] ) # significant strikes on the ground landed
        match_details['ss_ground_att'] = int( p1[18].split()[2] ) # significant strikes on the ground attempted
        match_details['o_ss_ground_hit'] = int( p2[18].split()[0] ) # opponent significant strikes on the ground landed
        match_details['o_ss_ground_att'] = int( p2[18].split()[2] ) # opponent significant strikes on the ground attempted

        match_details['player_1_url'] = p1[19] # player 1 /player-details/ url
        match_details['player_2_url'] = p2[19] # player 2 /player-details/ url
        
        match_details['match_url'] = match_url

        return match_details
    
    else:
        print('Failed to get match details.')
        
        match_details = None
        
        return match_details


In [42]:
def get_weight_class(weight):
    if weight <= 115:
        weightclass = 'Strawweight'
    elif weight <= 125:
        weightclass = 'Flyweight'
    elif weight <= 135:
        weightclass = 'Bantamweight'
    elif weight <= 145:
        weightclass = 'Featherweight'
    elif weight <= 155:
        weightclass = 'Lightweight'
    elif weight <= 170:
        weightclass = 'Welterweight'
    elif weight <= 185:
        weightclass = 'Middleweight'
    elif weight <= 205:
        weightclass = 'Light Heavyweight'
    elif weight > 205:
        weightclass = 'Heavyweight'
    else:
        weightclass = 'No weight data'
        
    return weightclass

In [52]:

def get_player_details(player_url):
    """Return list of stats scraped from /player-details/"""
    
    player_details = {}
    
    # Web request
    try:
        html = urlopen(player_url)
        bs = BeautifulSoup(html.read(), 'html.parser')
    except HTTPError as e:
        print(e)
    
    # player url
    player_details['player_url'] = player_url
    
    # player_name
    player_details['player_name'] = bs.find('span', {'class': 'b-content__title-highlight'}).text.strip()
    
    # wins, losses, ties, no-contests, total matches
    player_record = bs.find('span', {'class': 'b-content__title-record'}).text.strip()[8:].split('-')
    player_details['wins'] = int( player_record[0] )

    player_details['losses'] = int( player_record[1] )

    ties_nc = player_record[2] 
    if 'NC' in ties_nc:
        player_details['ties'] = int( ties_nc.split('(')[0] )
        player_details['nc'] = int( ties_nc.split('(')[1].split()[0] )
    else:
        player_details['ties'] = int( ties_nc.split('(')[0] )
        player_details['nc'] = 0
        
    player_details['total_matches'] = player_details['wins'] + \
                                      player_details['losses'] + \
                                      player_details['ties'] + \
                                      player_details['nc']
    
    # Physical statistics
    physical_stats = bs.find_all('li', {'class': 'b-list__box-list-item b-list__box-list-item_type_block'})

    # Using a number of try/except statements because not every player has every stat
    # Height in inches
    try: # not all player have heights
        height_list = physical_stats[0].text.split()[1:]
        height_feet = ''.join(char for char in height_list[0] if char.isdigit())
        height_inches = ''.join(char for char in height_list[1] if char.isdigit())
        player_details['height'] = int(height_feet) * 12 + int(height_inches)
    except:
        player_details['height'] = np.nan
        
    # Weight in lbs
    try:
        player_details['weight'] = int( physical_stats[1].text.split()[1] )
    except:
        player_details['weight'] = np.nan
        
    # Weight class
    try:
        weight_class = get_weight_class(player_details['weight'])
        player_details['weight_class'] = weight_class
    except:
        player_details['weight_class'] = 'No weight data'

    # Reach in inches
    try:
        player_details['reach'] = int( physical_stats[2].text.split()[1][0:2] ) # can only be two digits, nobody is taller than 8.3 ft
    except:
        player_details['reach'] = np.nan

    # Stance (Orthodox = 1, right hand and right leg are forward. Southpaw = 0, left hand and left leg are forward.)
    try:
        player_details['stance'] = physical_stats[3].text.split()[1]
        if player_details['stance'] == 'Orthodox': # boolean allows us to check if two players have the same stance
            player_details['stance'] = 1
        else:
            player_details['stance'] = 0
    except:
        player_details['stance'] = 1

    # Age
    try:
        player_details['age'] = 2022 - int( physical_stats[4].text.split()[-1] )
    except:
        player_details['age'] = np.nan

    # significant strikes landed per minute
    try:
        player_details['ss'] = float( physical_stats[5].text.split()[1] )
    except:
        player_details['ss'] = np.nan

    # percent of significant strikes landed 
    try:
        player_details['ss_acc'] = round( int( physical_stats[6].text.split()[2][:-1] ) / 100, 2)
    except:
        player_details['ss_acc'] = np.nan

    # significant strikes absorbed per minute
    try:
        player_details['ss_abs'] = float ( physical_stats[7].text.split()[1] )
    except:
        player_details['ss_abs'] = np.nan

    # percent of significant strikes defended/blocked
    try:
        player_details['ss_def'] = round( int( physical_stats[8].text.split()[-1][:-1] ) / 100, 2)
    except:
        player_details['ss_def'] = np.nan

    # takedowns landed per 15 minutes
    try:
        player_details['td'] = float( physical_stats[10].text.split()[-1] )
    except:
        player_details['td'] = np.nan

    # percent takedown accuracy
    try:
        player_details['td_acc'] = round( int ( physical_stats[11].text.split()[-1][:-1] ) / 100, 2 )
    except:
        player_details['td_acc'] = np.nan

    # percent takedown defense
    try:
        player_details['td_def'] = round( int ( physical_stats[12].text.split()[-1][:-1] ) / 100, 2 )
    except:
        player_details['td_def'] = np.nan

    # average submission attemtps per 15 minutes
    try:
        player_details['sub'] = float ( physical_stats[13].text.split()[-1] )
    except:
        player_details['sub'] = np.nan

    # Number of wins in the last 3 matches 
    prev = 0
    try:
        previous_matches = bs.find_all('i', {'class': 'b-flag__text'})
        if previous_matches[0].text == 'next': # if the first record shows the next match rather than a previous match
            previous_matches = previous_matches[1:4] # look at the last 3 matches and sum the wins
            for previous_match in previous_matches:
                if previous_match.text == 'win':
                    prev += 1
            player_details['prev'] = prev
            
        else:
            previous_matches = previous_matches[0:3] # change starting point because there is no next match
            for previous_match in previous_matches:
                if previous_match.text == 'win':
                    prev += 1
            player_details['prev'] = prev
    except:
        player_details['previous_matches'] = 0
        
    return player_details
    

In [6]:

# # Import previously-scraped data so as not to re-scrape existing matches/players.

# from os.path import exists

# if exists('/Users/jgronkowski/Documents/data_science/course_bd/Group Project/upcoming_event_urls_processed.csv'):
#     upcoming_event_urls_processed = pd.read_csv('upcoming_event_urls_processed.csv')
# else:
#     upcoming_event_urls_processed = []
    

# if exists('/Users/jgronkowski/Documents/data_science/course_bd/Group Project/completed_event_urls_processed.csv'):
#     completed_event_urls_processed = pd.read_csv('completed_event_urls_processed.csv')
# else:
#     completed_event_urls_processed = []
    

# if exists('/Users/jgronkowski/Documents/data_science/course_bd/Group Project/completed_match_urls_processed.csv'):
#     completed_match_urls_processed = pd.read_csv('completed_match_urls_processed.csv')
# else:
#     completed_match_urls_processed = []
    
    
# if exists('/Users/jgronkowski/Documents/data_science/course_bd/Group Project/upcoming_match_urls_processed.csv'):
#     upcoming_match_urls_processed = pd.read_csv('upcoming_match_urls_processed.csv')
# else:
#     upcoming_match_urls_processed = []

    
# if exists('/Users/jgronkowski/Documents/data_science/course_bd/Group Project/player_urls_processed.csv'):
#     player_urls_processed = pd.read_csv('player_urls_processed.csv')
# else:
#     player_urls_processed = []
    

# if exists('/Users/jgronkowski/Documents/data_science/course_bd/Group Project/completed_matches.csv'):
#     completed_matches_df = pd.read_csv('completed_matches.csv')
# else:
#     completed_matches_df = []


# if exists('/Users/jgronkowski/Documents/data_science/course_bd/Group Project/upcoming_matches.csv'):
#     upcoming_matches_df = pd.read_csv('upcoming_matches.csv')
# else:
#     upcoming_matches_df = []


# if exists('/Users/jgronkowski/Documents/data_science/course_bd/Group Project/players.csv'):
#     players_df = pd.read_csv('players.csv')
# else:
#     players_df = []
    

In [71]:
player_urls_processed = []
completed_matches_df = []
completed_match_urls_processed = []
completed_event_urls_processed = []
upcoming_event_urls_processed = []
players = {}

In [72]:

# # # CREATE DATAFRAMES OF COMPLETED MATCHES AND PLAYER DETAILS # # #

# start url: http://ufcstats.com/statistics/events/completed

# event urls: http://ufcstats.com/event-details/4bf3010fdeea9d93

# match urls: http://ufcstats.com/fight-details/4bf3010fdeea9d93

# Completed events: UFC events that happened in the past
completed_events_bs = get_bs('http://ufcstats.com/statistics/events/completed?page=all')
completed_events_urls = find_all_urls(completed_events_bs, regex_condition='.+/event-details/.+')
# pd.Series(list(completed_events_urls)).to_csv('completed_events_urlsx.csv')

# Completed matches: Matches that happened in the past that were scraped in this run.
completed_matches = []

# Each event has several matches
for event_url in completed_events_urls:
    
    if event_url in completed_event_urls_processed: 
        print('Event already processed:', event_url)
        continue
    
    # Scrape /event-details/
    print('Scraping event url:', event_url)
    event_bs = get_bs(event_url)
    
    # Returns a list ['23', 'January', '2020']
    event_date_list = event_bs.find_all('li', {'class': 'b-list__box-list-item'})[0].text.split()[1:]
    event_date = event_date_list[0] + ' ' + event_date_list[1] + ' ' + event_date_list[2]
    event_month = event_date_list[1]
    event_year = event_date_list[2]
    
    # Compile /fight-details/ urls on /event-details/ page
    print('Finding match urls')
    match_urls = find_all_urls(event_bs)
    
    if len(match_urls) > 0:
        
        print(f'Found {len(match_urls)} matches in the event.')

        # Scrape each /fight-details/ within /event-details/
        for match_url in match_urls:

            if match_url in completed_match_urls_processed:
                continue

            print(f'Getting match details: {match_url}')

            match_details = get_match_details(match_url)

            if match_details is None:
                
                completed_match_urls_processed.append(match_url)
                
                continue
                
            match_details['event_date'] = event_date
            
            match_details['event_month'] = event_month
            
            match_details['event_year'] = event_year
            
            # Get player 1 details from /fighter-details/
            if match_details['player_1_url'] in player_urls_processed:
                
                player_1_details = players[ match_details['player_1_url'] ]
                
                print(player_1_details['player_name'], 'player details already collected.')
            
            else:

                player_urls_processed.append(match_details['player_1_url'])

                player_1_details = get_player_details(match_details['player_1_url'])

                print('\nSaving player 1 details:', player_1_details['player_name'])

                players[ player_1_details['player_url'] ] = player_1_details

            # Get player 2 details from /fighter-details/
            if match_details['player_2_url'] in player_urls_processed:
                
                player_2_details = players[ match_details['player_2_url'] ]
                
                print(player_2_details['player_name'], 'player details already collected.')

            else:
                
                player_urls_processed.append(match_details['player_2_url'])

                player_2_details = get_player_details(match_details['player_2_url'])

                print('\nSaving player 2 details:', player_2_details['player_name'], '\n')

                players[ player_2_details['player_url'] ] = player_2_details

            # Create features of the differences between player 1 and player 2's player stats
            players_diffs = {}

            for key, value in player_1_details.items():

                if type(value) in (float, int):

                    players_diffs[key + '_diff'] = round( player_1_details[key] - player_2_details[key] , 2 )

            # Concatenate the differences in player 1 and 2 with match details for the final set of match features here.

            match_details = {**match_details, **players_diffs}

            # Concatenate the match_details to completed_matches
            completed_matches.append(match_details)

            completed_match_urls_processed.append(match_url)
        
    else: # if a match is not found (None) then skip next time and continue loop

        completed_match_urls_processed.append(match_url)
        continue
        
    completed_event_urls_processed.append(event_url)
    

Scraping event url: http://ufcstats.com/event-details/898337ef520fe4d3
Finding match urls
Found 11 matches in the event.
Getting match details: http://ufcstats.com/fight-details/d395828f5cb045a5

Saving player 1 details: Tony Ferguson

Saving player 2 details: Justin Gaethje 

Getting match details: http://ufcstats.com/fight-details/fcfaa28ed6888088

Saving player 1 details: Francis Ngannou

Saving player 2 details: Jairzinho Rozenstruik 

Getting match details: http://ufcstats.com/fight-details/b9abcce29378e5cc

Saving player 1 details: Donald Cerrone

Saving player 2 details: Anthony Pettis 

Getting match details: http://ufcstats.com/fight-details/f2520dd5457ab293

Saving player 1 details: Carla Esparza

Saving player 2 details: Michelle Waterson-Gomez 

Getting match details: http://ufcstats.com/fight-details/3f810c3433dddb80

Saving player 1 details: Niko Price

Saving player 2 details: Vicente Luque 

Getting match details: http://ufcstats.com/fight-details/08244974cf39ae38

Savi


Saving player 1 details: Rafael Fiziev

Saving player 2 details: Brad Riddell 

Getting match details: http://ufcstats.com/fight-details/c74b03337a8441ed

Saving player 1 details: Claudio Puelles

Saving player 2 details: Chris Gruetzemacher 

Getting match details: http://ufcstats.com/fight-details/723a8a8c82cab1c8

Saving player 1 details: Dusko Todorovic

Saving player 2 details: Maki Pitolo 

Getting match details: http://ufcstats.com/fight-details/1ce1a43ef68ffc7d
Louis Smolka player details already collected.

Saving player 2 details: Vince Morales 

Getting match details: http://ufcstats.com/fight-details/657b7da9c89352fe

Saving player 1 details: Alex Morono

Saving player 2 details: Mickey Gall 

Getting match details: http://ufcstats.com/fight-details/376dddfa82debbf4

Saving player 1 details: Zhalgas Zhumagulov

Saving player 2 details: Manel Kape 

Getting match details: http://ufcstats.com/fight-details/5d64044b985004e7

Saving player 1 details: Clay Guida

Saving player 


Saving player 2 details: Gunnar Nelson 

Getting match details: http://ufcstats.com/fight-details/824368db1ed8191f

Saving player 1 details: Alex Garcia

Saving player 2 details: Mike Swick 

Getting match details: http://ufcstats.com/fight-details/70290140b6a8e038
Chad Mendes player details already collected.

Saving player 2 details: Conor McGregor 

Getting match details: http://ufcstats.com/fight-details/b90eded8d6b65e8f

Saving player 1 details: Yosdenis Cedeno

Saving player 2 details: Cody Pfister 

Getting match details: http://ufcstats.com/fight-details/ecb4534c0066c5f3

Saving player 1 details: Robbie Lawler

Saving player 2 details: Rory MacDonald 

Getting match details: http://ufcstats.com/fight-details/2c5d329bdf182468
Cathal Pendred player details already collected.

Saving player 2 details: John Howard 

Getting match details: http://ufcstats.com/fight-details/a9d8ddb49dbe414b

Saving player 1 details: Thomas Almeida

Saving player 2 details: Brad Pickett 

Getting mat


Saving player 1 details: Eric Shelton

Saving player 2 details: Jenel Lausa 

Getting match details: http://ufcstats.com/fight-details/097bc98e15722998

Saving player 1 details: Alexander Volkanovski

Saving player 2 details: Shane Young 

Getting match details: http://ufcstats.com/fight-details/569e2c02f7699c0d

Saving player 1 details: Daniel Kelly

Saving player 2 details: Elias Theodorou 

Getting match details: http://ufcstats.com/fight-details/2060e8172f820d80

Saving player 1 details: Jessica-Rose Clark

Saving player 2 details: Bec Rawlings 

Getting match details: http://ufcstats.com/fight-details/5ebe8d3849273776
Tim Means player details already collected.

Saving player 2 details: Belal Muhammad 

Getting match details: http://ufcstats.com/fight-details/344bfe9c1ff511bb
Jake Matthews player details already collected.

Saving player 2 details: Bojan Velickovic 

Getting match details: http://ufcstats.com/fight-details/4b0aa5c67e69ce74
Fabricio Werdum player details already c


Saving player 1 details: Joe Solecki
Jared Gordon player details already collected.
Scraping event url: http://ufcstats.com/event-details/8a028648f3f0761d
Finding match urls
Found 11 matches in the event.
Getting match details: http://ufcstats.com/fight-details/5a09a7a3f2792d1a

Saving player 1 details: Felice Herrig

Saving player 2 details: Kailin Curran 

Getting match details: http://ufcstats.com/fight-details/3aace29fcc65ec51
Alex Oliveira player details already collected.

Saving player 2 details: James Moontasri 

Getting match details: http://ufcstats.com/fight-details/435c93cb89016fd1

Saving player 1 details: Jason Knight

Saving player 2 details: Jim Alers 

Getting match details: http://ufcstats.com/fight-details/8167500af262bba5

Saving player 1 details: Frankie Saenz
Eddie Wineland player details already collected.
Getting match details: http://ufcstats.com/fight-details/43fbc59edc7dfa9f

Saving player 1 details: Luis Henrique

Saving player 2 details: Dmitrii Smoliakov 

...

Jonathan Pearce player details already collected.
Kai Kamaka player details already collected.
Getting match details: http://ufcstats.com/fight-details/0c27552ea7bc8c8a
Anderson Dos Santos player details already collected.
Martin Day player details already collected.
Getting match details: http://ufcstats.com/fight-details/711f00d287344c77
Gina Mazany player details already collected.
Rachael Ostovich player details already collected.
Getting match details: http://ufcstats.com/fight-details/32a7da2f34ae3803
Parker Porter player details already collected.
Josh Parisian player details already collected.
Getting match details: http://ufcstats.com/fight-details/8868957c1735bcf0
Malcolm Gordon player details already collected.
Sumudaerji player details already collected.
Getting match details: http://ufcstats.com/fight-details/e64d80dcc6853ea0
Nate Maness player details already collected.
Luke Sanders player details already collected.
Getting match details: http://ufcstats.com/fight-details

Yusuke Kasuya player details already collected.
Nick Hein player details already collected.
Getting match details: http://ufcstats.com/fight-details/1c5bed46920ab3e1
Diego Brandao player details already collected.
Katsunori Kikuno player details already collected.
Getting match details: http://ufcstats.com/fight-details/34fd6ac116645ae6
Josh Barnett player details already collected.
Roy Nelson player details already collected.
Getting match details: http://ufcstats.com/fight-details/6712440cd01dffdb
Gegard Mousasi player details already collected.
Uriah Hall player details already collected.
Getting match details: http://ufcstats.com/fight-details/b82b243982fcb2ac
Naoyuki Kotani player details already collected.
Kajan Johnson player details already collected.
Getting match details: http://ufcstats.com/fight-details/85e1b21ea88fe7e3
Keita Nakamura player details already collected.
Li Jingliang player details already collected.
Scraping event url: http://ufcstats.com/event-details/39c568

Rafael Dos Anjos player details already collected.
Tyson Griffin player details already collected.
Getting match details: http://ufcstats.com/fight-details/ae68274ab6f78cd8
Carlos Condit player details already collected.
Martin Kampmann player details already collected.
Getting match details: http://ufcstats.com/fight-details/c642640db89fb033
Tim Credeur player details already collected.
Nick Catone player details already collected.
Getting match details: http://ufcstats.com/fight-details/9c7a67ce1d6a01f9
Gleison Tibau player details already collected.
Jeremy Stephens player details already collected.
Getting match details: http://ufcstats.com/fight-details/4b9203b86f0aa870
Matt Horwich player details already collected.
Ricardo Almeida player details already collected.
Scraping event url: http://ufcstats.com/event-details/0c1773639c795466
Finding match urls
Found 11 matches in the event.
Getting match details: http://ufcstats.com/fight-details/36032308b7e86fd0
Raquel Pennington player 

Kennedy Nzechukwu player details already collected.
Da-Un Jung player details already collected.
Getting match details: http://ufcstats.com/fight-details/a27a355f52883f3e
Collin Anglin player details already collected.
Sean Woodson player details already collected.
Getting match details: http://ufcstats.com/fight-details/73c97d5c314f1270
Julio Arce player details already collected.
Song Yadong player details already collected.
Scraping event url: http://ufcstats.com/event-details/f65a0eb902f9476b
Finding match urls
Scraping event url: http://ufcstats.com/event-details/3b2485c8d5c8b580
Finding match urls
Found 13 matches in the event.
Getting match details: http://ufcstats.com/fight-details/9cdfcd164b48f55e
Mason Jones player details already collected.
Alan Patrick player details already collected.
Getting match details: http://ufcstats.com/fight-details/5c0e5d850d8e661f
Santiago Ponzinibbio player details already collected.
Miguel Baeza player details already collected.
Getting match d

Finding match urls
Found 12 matches in the event.
Getting match details: http://ufcstats.com/fight-details/86892d114b204bf3
Ryan Janes player details already collected.
Jack Marshman player details already collected.
Getting match details: http://ufcstats.com/fight-details/a77950d6a0a451f4
Justin Willis player details already collected.

Saving player 2 details: James Mulheron 

Getting match details: http://ufcstats.com/fight-details/7e7fba47f511f8ad
Charlie Ward player details already collected.
Galore Bofando player details already collected.
Getting match details: http://ufcstats.com/fight-details/d49d2c810583a56a
Amanda Lemos player details already collected.
Leslie Smith player details already collected.
Getting match details: http://ufcstats.com/fight-details/8fd14eb227688467
Alexandre Pantoja player details already collected.
Neil Seery player details already collected.
Getting match details: http://ufcstats.com/fight-details/0f8b2f7299b5e114
Khalil Rountree Jr. player details 

In [83]:
print(len(completed_matches))
print(len(completed_event_urls_processed))
completed_matches[0]

6891
628


{'player_1_name': 'Tony Ferguson',
 'player_2_name': 'Justin Gaethje',
 'weight_class': 'UFC Interim Lightweight Title',
 'win': 0,
 'duration': 25,
 'kd': 0,
 'o_kd': 0,
 'ss_hit': 136,
 'ss_att': 296,
 'o_ss_hit': 143,
 'o_ss_att': 197,
 'ss_perc': 0.45,
 'o_ss_perc': 0.72,
 's_hit': 136,
 's_att': 296,
 'o_s_att': 197,
 'o_s_hit': 143,
 'td_hit': 0,
 'td_att': 0,
 'o_td_hit': 0,
 'o_td_att': 0,
 'td_perc': 0.0,
 'o_td_perc': 0.0,
 'sub_att': 0,
 'o_sub_att': 0,
 'rev': 0,
 'o_rev': 0,
 'ctrl': 0,
 'o_ctrl': 0,
 'ss_head_hit': 64,
 'ss_head_att': 212,
 'o_ss_head_hit': 100,
 'o_ss_head_att': 153,
 'ss_body_hit': 36,
 'ss_body_att': 43,
 'o_ss_body_hit': 13,
 'o_ss_body_att': 14,
 'ss_leg_hit': 36,
 'ss_leg_att': 41,
 'o_ss_leg_hit': 30,
 'o_ss_leg_att': 30,
 'ss_dist_hit': 136,
 'ss_dist_att': 296,
 'o_ss_dist_hit': 143,
 'o_ss_dist_att': 197,
 'ss_clinch_hit': 0,
 'ss_clinch_att': 0,
 'o_ss_clinch_hit': 0,
 'o_ss_clinch_att': 0,
 'ss_ground_hit': 0,
 'ss_ground_att': 0,
 'o_ss_groun

In [74]:

# # # CREATE DATAFRAME OF UPCOMING MATCHES # # #

# Upcoming events: The next few UFC events that have been posted
upcoming_events_bs = get_bs('http://ufcstats.com/statistics/events/upcoming')
upcoming_events_urls = find_all_urls(upcoming_events_bs, regex_condition='.+/event-details/.+')
pd.Series(list(upcoming_events_urls)).to_csv('upcoming_event_urls.csv')

# Upcoming matches: Matches that are scheduled to happen that were scraped in this run.
upcoming_matches = []

# Group player urls into lists of length two (per match), where player_1 is first url and player_2 is second
def chunks(lst, n):
    """Yield successive n-sized chunks from lst."""

    for i in range(0, len(lst), n):

        yield lst[i:i + n]

# Scrape upcoming matches page
upcoming_events_bs = get_bs('http://ufcstats.com/statistics/events/upcoming?page=all')
upcoming_events_urls = find_all_urls(upcoming_events_bs, regex_condition='.+/event-details/.+')

for upcoming_event_url in upcoming_events_urls:
    
    if upcoming_event_url in upcoming_event_urls_processed:
        continue

    # Scrape /event-details/
    print('Scraping event url:', upcoming_event_url)
    event_bs = get_bs(event_url)

    # Compile /fight-details/ urls on /event-details/ page
    print('Finding match urls')

    player_url_tags = event_bs.find_all('a', {'href': re.compile('.+/fighter-details/.+')})

    if len(player_url_tags) == 0:
        print('Error. No players found on event page.')
        pass

    player_urls = []

    for i in range(len(player_url_tags)): # extract the urls from the tags and save to player_urls

        player_urls.append(player_url_tags[i]['href'])

    matches = list(chunks(player_urls, 2)) # create a list of lists of length 2, representing each match

    for player_url in matches:

        if player_url[0] not in players:

            player_1_details = get_player_details(player_url[0])

            players[ player_1_details['player_url'] ] = player_1_details
            
        else:
            
            player_1_details = players[ player_url[0] ]

        if player_url[1] not in players:

            player_2_details = get_player_details(player_url[1])

            players[ player_2_details['player_url'] ] = player_2_details
            
        else:
            
            player_2_details = players[ player_url[1] ]

        players_diffs = {}

        players_diffs['player_1_name'] = player_1_details['player_name']
        players_diffs['player_2_name'] = player_2_details['player_name']
        players_diffs['player_1_url'] = player_1_details['player_url']
        players_diffs['player_2_url'] = player_2_details['player_url']

        for key, value in player_1_details.items():

            if type(value) in (float, int):

                players_diffs[key] = round( player_1_details[key] - player_2_details[key] , 2 )

        upcoming_matches.append(players_diffs)
        
    upcoming_event_urls_processed.append(upcoming_event_url)
        

Scraping event url: http://ufcstats.com/event-details/56ec58954158966a
Finding match urls
Scraping event url: http://ufcstats.com/event-details/01dd4cdc2446f665
Finding match urls
Scraping event url: http://ufcstats.com/event-details/f65a0eb902f9476b
Finding match urls
Scraping event url: http://ufcstats.com/event-details/5717efc6f271cd52
Finding match urls
Scraping event url: http://ufcstats.com/event-details/2e2cdb6e9eb84bb9
Finding match urls


In [183]:
# Add weight classes to completed_matches:

for i in range(len(completed_matches)):
    
    weight_class = players[ completed_matches[i]['player_1_url']]['weight_class']
    
    completed_matches[i]['weight_class'] = weight_class

# Add weight classes to upcoming_matches

for i in range(len(upcoming_matches)):
    
    weight_class = players[upcoming_matches[i]['player_1_url']]['weight_class']

    upcoming_matches[i]['weight_class'] = weight_class

print(completed_matches[0]['weight_class'])
print(upcoming_matches[0]['weight_class'])

Lightweight
Welterweight


In [190]:
completed_matches

[{'player_1_name': 'Tony Ferguson',
  'player_2_name': 'Justin Gaethje',
  'weight_class': 'Lightweight',
  'win': 0,
  'duration': 25,
  'kd': 0,
  'o_kd': 0,
  'ss_hit': 136,
  'ss_att': 296,
  'o_ss_hit': 143,
  'o_ss_att': 197,
  'ss_perc': 0.45,
  'o_ss_perc': 0.72,
  's_hit': 136,
  's_att': 296,
  'o_s_att': 197,
  'o_s_hit': 143,
  'td_hit': 0,
  'td_att': 0,
  'o_td_hit': 0,
  'o_td_att': 0,
  'td_perc': 0.0,
  'o_td_perc': 0.0,
  'sub_att': 0,
  'o_sub_att': 0,
  'rev': 0,
  'o_rev': 0,
  'ctrl': 0,
  'o_ctrl': 0,
  'ss_head_hit': 64,
  'ss_head_att': 212,
  'o_ss_head_hit': 100,
  'o_ss_head_att': 153,
  'ss_body_hit': 36,
  'ss_body_att': 43,
  'o_ss_body_hit': 13,
  'o_ss_body_att': 14,
  'ss_leg_hit': 36,
  'ss_leg_att': 41,
  'o_ss_leg_hit': 30,
  'o_ss_leg_att': 30,
  'ss_dist_hit': 136,
  'ss_dist_att': 296,
  'o_ss_dist_hit': 143,
  'o_ss_dist_att': 197,
  'ss_clinch_hit': 0,
  'ss_clinch_att': 0,
  'o_ss_clinch_hit': 0,
  'o_ss_clinch_att': 0,
  'ss_ground_hit': 0,
 

In [164]:
import math        

# TO DO: Update get_player_details function to pull all weight classes as some have been missed.
# TEMP FIX: Fix for missing weightclasses

for i in range(players_df.shape[0]):
    
    if math.isnan(players_df.iloc[i]['weight']):
        continue
    
    if isinstance(players_df.iloc[i]['weight'], float):
        
        weight_class = get_weight_class(int(players_df.iloc[i]['weight']))
        players_df.iloc[i]['weight_class'] = weight_class


### NOTE
- These files will not save in Google Drive upon running the next cell.
- Saving output files as CSVs will be developed in Google Cloud Platform.

player_1_name            player_2_name   weight_class  win  duration  \
0       Tony Ferguson           Justin Gaethje    Lightweight    0        25   
1     Francis Ngannou    Jairzinho Rozenstruik    Heavyweight    1        15   
2      Anthony Pettis           Donald Cerrone    Lightweight    1        15   
3       Carla Esparza  Michelle Waterson-Gomez    Strawweight    1        15   
4       Vicente Luque               Niko Price   Welterweight    1        15   
...               ...                      ...            ...  ...       ...   
6886      Danny Henry            Daniel Teymur  Featherweight    1        15   
6887       Stevie Ray              Paul Felder    Lightweight    0        15   
6888    Danny Roberts               Bobby Nash   Welterweight    1        15   
6889      Joanne Wood         Cynthia Calvillo      Flyweight    0        15   
6890    Gunnar Nelson     Santiago Ponzinibbio   Welterweight    0        25   

      kd  o_kd  ss_hit  ss_att  o_ss_hit  ...  age_diff  ss_diff  ss_acc_diff  \
0      0     0     136     296       143  ...       4.0    -2.39        -0.15   
1      1     0       6      13         5  ...       2.0    -0.47        -0.04   
2      0     0      63     113        62  ...       4.0     1.36        -0.01   
3      0     0      45     103        44  ...      -1.0    -1.44        -0.08   
4      1     0     130     237       129  ...       2.0    -0.01        -0.10   
...   ..   ...     ...     ...       ...  ...       ...      ...          ...   
6886   1     0      93     174        69  ...       0.0    -2.12        -0.05   
6887   0     1       5       9        23  ...       6.0    -0.03         0.00   
6888   1     0      24      65        25  ...      -3.0     0.34        -0.03   
6889   0     0      63     176        54  ...       2.0     2.60         0.11   
6890   0     1       5       7         7  ...       2.0     3.17        -0.19   

      ss_abs_diff  ss_def_diff  td_diff  td_acc_diff  td_def_diff  sub_diff  \
0           -3.90         0.03     0.44         0.41        -0.09       1.0   
1           -1.08        -0.04     0.76         0.62        -0.04       0.3   
2            1.04        -0.01     0.55        -0.17         0.13       0.1   
3           -1.40         0.05     1.79         0.02        -0.20      -0.5   
4            0.06        -0.04     0.19        -0.30         0.03      -0.1   
...           ...          ...      ...          ...          ...       ...   
6886        -0.23         0.11    -0.18        -0.15         0.10      -1.9   
6887         0.51        -0.06    -0.46        -0.18         0.09      -0.4   
6888         0.45         0.00     2.11         0.23         0.43       1.3   
6889         0.59        -0.13    -0.35         0.11        -0.16      -0.5   
6890         1.72         0.10    -1.30        -0.29        -0.06      -0.9   

      prev_diff  
0            -1  
1             2  
2            -2  
3             1  
4             0  
...         ...  
6886          0  
6887         -1  
6888         -1  
6889          0  
6890          0  

[6891 rows x 78 columns]

In [201]:
# Create or update dataframes and save to CSVs.


# Completed matches
completed_matches_to_add_list = [i for i in completed_matches if i is not None]
completed_matches_to_add_df = pd.DataFrame(completed_matches_to_add_list)

if len(completed_matches_df) == 0: # if this variable is a blank list rather than a dataframe of existing matches
    completed_matches_df = completed_matches_to_add_df
else:
    completed_matches_df = pd.concat([completed_matches_df, completed_matches_to_add_df]).drop_duplicates()

completed_matches_df.loc[ ~ completed_matches_df.match_url.isna()].to_csv('completed_matches.csv')


# Upcoming matches
upcoming_matches_to_add_list = [i for i in upcoming_matches if i is not None]
upcoming_matches_to_add_df = pd.DataFrame(upcoming_matches_to_add_list)

if len(upcoming_matches_df) == 0: # if this variable is a blank list rather than a dataframe of existing matches
    upcoming_matches_df = upcoming_matches_to_add_df
else:
    upcoming_matches_df = pd.concat([upcoming_matches_df, upcoming_matches_to_add_df]).drop_duplicates()

upcoming_matches_df.to_csv('upcoming_matches.csv')


# Update or create a dataframe of players and save to CSV.
players_to_add_df = pd.DataFrame(players).T.reset_index().drop('index', axis=1)

if len(players_df) == 0:
    players_df = players_to_add_df
else:
    players_df = pd.concat([players_df, players_to_add_df]).drop_duplicates()

# players_df = players_df.drop('Unnamed: 0', axis=1)
players_df.to_csv('players.csv')


# player_urls_processed


# Completed match urls processed


# Completed event urls processed


# Upcoming match urls processed


# Upcoming event urls processed

In [203]:
upcoming_matches_df.head()

player_1_name  player_2_name  \
0  Santiago Ponzinibbio  Gunnar Nelson   
1      Cynthia Calvillo    Joanne Wood   
2           Paul Felder     Stevie Ray   
3         Jack Marshman     Ryan Janes   
4   Khalil Rountree Jr.     Paul Craig   

                                        player_1_url  \
0  http://ufcstats.com/fighter-details/6d1bffff14...   
1  http://ufcstats.com/fighter-details/98215d037b...   
2  http://ufcstats.com/fighter-details/e5010b1b94...   
3  http://ufcstats.com/fighter-details/045f25b3a4...   
4  http://ufcstats.com/fighter-details/749f572d1d...   

                                        player_2_url  wins  losses  ties  nc  \
0  http://ufcstats.com/fighter-details/fd55393021...    11       1    -1   0   
1  http://ufcstats.com/fighter-details/12f91bfa8f...    -6      -3     1   0   
2  http://ufcstats.com/fighter-details/31a13532e7...    -6      -3     0   0   
3  http://ufcstats.com/fighter-details/b59037262c...    13       7     0   0   
4  http://ufcstats.com/fighter-details/eabf206b16...    -4       0    -1   1   

   total_matches  height  ...    ss  ss_acc  ss_abs  ss_def    td  td_acc  \
0             11       1  ...  3.17   -0.19    1.72    0.10 -1.30   -0.29   
1             -8      -2  ... -2.60   -0.11   -0.59    0.13  0.35   -0.11   
2             -9       1  ... -0.03    0.00    0.51   -0.06 -0.46   -0.18   
3             20      -3  ... -4.95   -0.23   -1.34   -0.03 -0.35   -1.00   
4             -4      -2  ...  1.20   -0.08    1.40    0.03 -1.85   -0.20   

   td_def  sub  prev       weight_class  
0   -0.06 -0.9     0       Welterweight  
1    0.16  0.5     0          Flyweight  
2    0.09 -0.4    -1        Lightweight  
3   -0.38  0.0     0       Middleweight  
4    0.04 -1.6     1  Light Heavyweight  

[5 rows x 24 columns]

In [204]:
completed_matches_df.head()

player_1_name            player_2_name  weight_class  win  duration  kd  \
0    Tony Ferguson           Justin Gaethje   Lightweight    0        25   0   
1  Francis Ngannou    Jairzinho Rozenstruik   Heavyweight    1        15   1   
2   Anthony Pettis           Donald Cerrone   Lightweight    1        15   0   
3    Carla Esparza  Michelle Waterson-Gomez   Strawweight    1        15   0   
4    Vicente Luque               Niko Price  Welterweight    1        15   1   

   o_kd  ss_hit  ss_att  o_ss_hit  ...  age_diff  ss_diff  ss_acc_diff  \
0     0     136     296       143  ...       4.0    -2.39        -0.15   
1     0       6      13         5  ...       2.0    -0.47        -0.04   
2     0      63     113        62  ...       4.0     1.36        -0.01   
3     0      45     103        44  ...      -1.0    -1.44        -0.08   
4     0     130     237       129  ...       2.0    -0.01        -0.10   

   ss_abs_diff  ss_def_diff  td_diff  td_acc_diff  td_def_diff  sub_diff  \
0        -3.90         0.03     0.44         0.41        -0.09       1.0   
1        -1.08        -0.04     0.76         0.62        -0.04       0.3   
2         1.04        -0.01     0.55        -0.17         0.13       0.1   
3        -1.40         0.05     1.79         0.02        -0.20      -0.5   
4         0.06        -0.04     0.19        -0.30         0.03      -0.1   

   prev_diff  
0         -1  
1          2  
2         -2  
3          1  
4          0  

[5 rows x 78 columns]

In [206]:
players_df.head()

player_url     player_name wins  \
0  http://ufcstats.com/fighter-details/0e9869d712...      Sam Adkins    7   
1  http://ufcstats.com/fighter-details/271fe91f4b...        Don Frye   20   
2  http://ufcstats.com/fighter-details/07a18ae55d...   Paul Varelans    9   
3  http://ufcstats.com/fighter-details/df85d6ec34...     Joe Moreira    2   
4  http://ufcstats.com/fighter-details/ea398c802d...  Thomas Ramirez    0   

  losses ties nc total_matches height weight reach  ...    ss ss_acc ss_abs  \
0     20    2  0            29   75.0  225.0   NaN  ...   0.0    0.0    0.0   
1      9    1  1            31   73.0  219.0   NaN  ...  2.87   0.64   3.57   
2      9    0  0            18   80.0  300.0   NaN  ...   0.0    0.0    0.0   
3      2    0  0             4   71.0  195.0   NaN  ...   0.0    0.0    0.0   
4      1    0  0             1   73.0  410.0   NaN  ...   0.0    0.0    0.0   

  ss_def    td td_acc td_def  sub prev       weight_class  
0    0.0   0.0    0.0    0.0  0.0    1        Heavyweight  
1   0.37  0.91   0.57   0.45  0.7    0        Heavyweight  
2    0.0   0.0    0.0    0.0  0.0    1        Heavyweight  
3    0.0   0.0    0.0    0.0  0.0    1  Light Heavyweight  
4    0.0   0.0    0.0    0.0  0.0    0        Heavyweight  

[5 rows x 22 columns]